In [11]:
import urllib
import json
import pandas as pd
import numpy as np
import warnings
import pickle
from datetime import datetime
from datetime import timedelta
import statistics
warnings.filterwarnings('ignore')

In [19]:
PICKLE_PATH = 'hopkins_conf_augmented0904.pkl'
RESULT_PATH = 'hopkins.conf.0904.withgr.pkl'

###### Open pickle file

In [13]:


hopkins_confirmed = pd.DataFrame()
 
hpcon_rates=pd.DataFrame()

with open(PICKLE_PATH, 'rb') as file:
    hopkins_confirmed = pickle.load(file)
    
hopkins_confirmed
hopkins_confirmed.insert(7,column='last relevant date',value=' ')

hopkins_confirmed.insert(7,column='first_7',value=np.nan)  # first 7 days after 5% inf croseed (if exist)


    
        

#hpcon_datarows = pd.DataFrame()
#hpcon_datarows =hopkins_confirmed.index
    
#for row in hopkins_confirmed.iterrows():
#     hpcon_datarows.append(row)

#hpcon_datarows

In [14]:
datarows = [row for row in hopkins_confirmed.iterrows()  if row[0][1]=='data']
#hopkins_confirmed.insert(7,column='last relevant date',value=np.nan)

 


### Obtain a list of dates (string of columns names which are dates , assumed to be a continouos sequence in the DF)


cur=0

for name in hopkins_confirmed.columns :
    if '2020' in name and '/' in name: # this is a date!
        datefound=True
        break
    cur +=1  
if datefound == False:
    print ('date not found in DF columns')
else:
    print ('first date is',name, 'offset',cur )
    firstdate=name
    firstdate_offset=cur 
    
rvrscur=len(hopkins_confirmed.columns)

for name in hopkins_confirmed.columns[::-1]:                #this loop will allow columns which are not dates right of dates
    if '2020' in name and '/' in name: # this is a date!
        break # this is  a date...
    else:
        rvrscur -=1
print ('rvrscur col',hopkins_confirmed.columns[rvrscur-1])
valid_dates=hopkins_confirmed.columns[cur:rvrscur]         # valid dates - all the dates in the index

print ('dates',valid_dates)
print ('last',valid_dates[-1])
 

for row in datarows:
    #print (row[0],row[0][1])
    ratios=[0]
    totals=[]
    actual_dates=[]
    
    for cursor in range (len(valid_dates)-1):
        p=row[1][valid_dates[cursor]]
        q=row[1][valid_dates[cursor+1]  ]
        actual_dates.append(valid_dates[cursor])
        if p > 0:
            ratios.append (round(q/p - 1,4 ))
            totals.append (p)
        else:
            if q>0:
                ratios.append (0)           # the first gr is set to 0  and will most often get removed due to
                                            # totals less then 5 pct,
            else: ratios.append(0)          #  0 growth between two zeros...
            totals.append(0)
            
    #ratios=[0]+ratios  # so that each growth rate 'sits' under its 'total' and is the growth between this and the 
                       # previous
    totals.append(row[1][valid_dates[-1]]) # add the last total to list
    actual_dates.append(valid_dates[-1])
           
    print ('==========')        
    print  ('new',row[1]['Province_State'],row[1][ 'Country_Region'])
    print ('totals',totals)
    print ('ratios',ratios)
       
    if max(totals)<20:
        print ('SKIP')
        continue    ###  if no day with 20 or more, skip this region,  small numbers 
    print ('NO SKIP')
        
   
    print (row[1]['Province_State'],row[1][ 'Country_Region'],ratios,totals)
    print ('lens',len(ratios),len(totals))
    maxt=max(totals)
    few=maxt/20
    print (row[1]['Province_State'],row[1][ 'Country_Region'],maxt,few)
    # here , find the 5% seperator
    few_seperator = -1
    for cursor in range (len(totals)-1):
        if  (totals[cursor] <=few ) and (totals [cursor+1]>=few):
            few_seperator=cursor
            break
    if few_seperator >=0 :
        t_sample=totals[cursor+1:]
        t_ratios=ratios[cursor+1:]
        actual_dates=actual_dates[cursor+1:]
        five_pct_name=actual_dates[0]
        
        print ('five pct', five_pct_name) 
    else:
        five_pct_name=actual_dates[0]  # this is the complete actual_dates
        print ('five pct not found',five_pct_name )
 
    #   find if there is a sequence of growth rate lower than 2% per day (from the end )  remove it if found
    
    for cur in range (len(t_ratios)):
        maxright=max(t_ratios[cur:])
        if   (maxright>0.02):
            continue
        else:
            print ('maxright ,cur, len ratios, rightside',maxright,cur,len(t_ratios),t_ratios[cur:],t_sample[cur:] )
            break
    
    
    last_relevant_sample=actual_dates[ -1]  # overriden if cut   
    if cur < len(t_ratios)-1:
     
        print ('cut right side len befor , len after',len(t_ratios),cur+1)
        
        t_ratios=t_ratios [:cur+1]
        t_sample=t_sample [:cur+1]
        actual_dates=actual_dates[:cur+1]
        last_relevant_sample=actual_dates[ -1]
        
    else: print ('nothing was cut')
            
    
    sorted_sample=t_sample.sort()
    
    
    print ('sample size',len(t_sample),t_sample,t_ratios)
    
    med=statistics.median(t_ratios)
    
    lower=np.percentile(t_ratios,25)
    upper=np.percentile(t_ratios,75)
    
    print ('lower, median, upper',lower,med,upper)
    
    colslen=len(hopkins_confirmed)
    daycount=0
    sevendays=[]
    
    for smpl in t_sample:
        if smpl< few : continue
        else:
            daycount +=1
            if daycount==8 : break
            else: sevendays.append(smpl)
    if daycount==8:
        if sevendays[0]>0:
            
            seven_days_growth=(sevendays[-1]/sevendays[0])-1
    
        else:
            daycount=0
    else: daycount=0
     
    
    coord=row [0][0]
    if daycount>0:
        hopkins_confirmed.loc[coord, 'first_7']['data'] = seven_days_growth
        print ( 'Debug 7 ', seven_days_growth)
        
    hopkins_confirmed.loc[coord, '5%_Date']['data'] = five_pct_name
    hopkins_confirmed.loc[coord, 'last relevant date']['data']=last_relevant_sample
    hopkins_confirmed.loc[coord, 'GF_Q1']['data']=lower
    hopkins_confirmed.loc[coord, 'GF_Q2']['data']=med
    hopkins_confirmed.loc[coord, 'GF_Q3']['data']=upper
    print ('Debug 0 ',hopkins_confirmed.loc[coord,'GF_Q1']['data'], hopkins_confirmed.loc[coord,'GF_Q3']['data'])
    
     
    #hopkins_confirmed.loc[(row[0][0],'Growth rates'),:]=   (  pd.Series([np.nan]*colslen) )     # add the row
    #print  ('row added ',row[0][0],row[0][1])
    
    #xx=hopkins_confirmed.loc[(row[0][0])].loc['data'].at['5%_Date'] 
        
    #hopkins_confirmed.loc[(row[0][0])].loc['data'].at['5%_Date'] =five_pct_name
    #xx2=hopkins_confirmed.loc[(row[0][0])].loc['data'].at['5%_Date'] 
    
    #print ('xx, xx2,xx3',xx,xx2 ) 
    #print ('last',last_relevant_sample)
    ##hopkins_confirmed.at[(row[0][0],'Growth rates'),'last relevant date']=last_relevant_sample
    #hopkins_confirmed.at[(row[0][0],'Growth rates'),'GF_Q1']=lower
    #hopkins_confirmed.at[(row[0][0],'Growth rates'),'GF_Q2']=med
    #hopkins_confirmed.at[(row[0][0],'Growth rates'),'GF_Q3']=upper
    #for cursor in range(len(actual_dates)):
    #    date=actual_dates[cursor]
    #    hopkins_confirmed.at[(row[0][0],'Growth rates'),date]=t_ratios[cursor]
    
    print ('DEBUG1' , row[1]['Province_State'],row[1][ 'Country_Region'],maxt,few)
    print ('DEBUG2' , lower, med, upper,five_pct_name,len(actual_dates),len(t_ratios))
    print ('DEBUG3', t_ratios)
    print ('DEBUG4', t_sample)
    print ('DEBUG5',hopkins_confirmed.loc[(row[0][0])])
    
    
      
        
hopkins_confirmed 
                 
 

first date is 1/22/2020 offset 16
rvrscur col 4/7/2020
dates Index(['1/22/2020', '1/23/2020', '1/24/2020', '1/25/2020', '1/26/2020',
       '1/27/2020', '1/28/2020', '1/29/2020', '1/30/2020', '1/31/2020',
       '2/1/2020', '2/2/2020', '2/3/2020', '2/4/2020', '2/5/2020', '2/6/2020',
       '2/7/2020', '2/8/2020', '2/9/2020', '2/10/2020', '2/11/2020',
       '2/12/2020', '2/13/2020', '2/14/2020', '2/15/2020', '2/16/2020',
       '2/17/2020', '2/18/2020', '2/19/2020', '2/20/2020', '2/21/2020',
       '2/22/2020', '2/23/2020', '2/24/2020', '2/25/2020', '2/26/2020',
       '2/27/2020', '2/28/2020', '2/29/2020', '3/1/2020', '3/2/2020',
       '3/3/2020', '3/4/2020', '3/5/2020', '3/6/2020', '3/7/2020', '3/8/2020',
       '3/9/2020', '3/10/2020', '3/11/2020', '3/12/2020', '3/13/2020',
       '3/14/2020', '3/15/2020', '3/16/2020', '3/17/2020', '3/18/2020',
       '3/19/2020', '3/20/2020', '3/21/2020', '3/22/2020', '3/23/2020',
       '3/24/2020', '3/25/2020', '3/26/2020', '3/27/2020', '3/28/20

Debug 0  0.074 0.24715
DEBUG1 nan Argentina 1628.0 81.4
DEBUG2 0.074 0.13929999999999998 0.24715 3/19/2020 20 20
DEBUG3 [0.2278, 0.3196, 0.2344, 0.6835, 0.1316, 0.2857, 0.0, 0.2972, 0.1733, 0.1715, 0.0797, 0.1007, 0.2854, 0.0, 0.075, 0.1165, 0.147, 0.0, 0.071, 0.0476]
DEBUG4 [97.0, 128.0, 158.0, 266.0, 301.0, 387.0, 387.0, 502.0, 589.0, 690.0, 745.0, 820.0, 1054.0, 1054.0, 1133.0, 1265.0, 1451.0, 1451.0, 1554.0, 1628.0]
DEBUG5              Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                    NaN      Argentina  21.998701  45.376623   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases   first_7  \
information                  

Debug 0  0.11025 0.20925
DEBUG1 nan Chile 5116.0 255.8
DEBUG2 0.11025 0.1436 0.20925 3/20/2020 19 19
DEBUG3 [0.8235, 0.2373, 0.1769, 0.1804, 0.2359, 0.2386, 0.1436, 0.2328, 0.1857, 0.1205, 0.1449, 0.118, 0.107, 0.1231, 0.0978, 0.1135, 0.0745, 0.0769, 0.0625]
DEBUG4 [434.0, 537.0, 632.0, 746.0, 922.0, 1142.0, 1306.0, 1610.0, 1909.0, 2139.0, 2449.0, 2738.0, 3031.0, 3404.0, 3737.0, 4161.0, 4471.0, 4815.0, 5116.0]
DEBUG5              Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                    NaN          Chile  19.735065  56.662338   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases   first_7  \
information                            

Debug 0  0.0278 0.2759
DEBUG1 South Australia Australia 411.0 20.55
DEBUG2 0.0278 0.1049 0.2759 3/16/2020 21 21
DEBUG3 [0.45, 0.0, 0.2759, 0.1351, 0.1905, 0.34, 0.4925, 0.34, 0.2687, 0.0, 0.3824, 0.0936, 0.1167, 0.0418, 0.0201, 0.1049, 0.089, 0.0, 0.079, 0.0278, 0.0]
DEBUG4 [29.0, 29.0, 37.0, 42.0, 50.0, 67.0, 100.0, 134.0, 170.0, 170.0, 235.0, 257.0, 287.0, 299.0, 305.0, 337.0, 367.0, 367.0, 396.0, 407.0, 407.0]
DEBUG5                Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                          
data          South Australia      Australia   20.07013  58.376623   
avg_d_RH                  NaN            NaN        NaN        NaN   
avg_d_precip              NaN            NaN        NaN        NaN   
avg_d_tmp                 NaN            NaN        NaN        NaN   
avg_d_wind                NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases   first_7  \
information           

Debug 7  3.2857142857142856
Debug 0  0.0288 0.2452
DEBUG1 Western Australia Australia 460.0 23.0
DEBUG2 0.0288 0.12385 0.2452 3/16/2020 22 22
DEBUG3 [0.6471, 0.1071, 0.129, 0.4857, 0.2308, 0.4062, 0.3333, 0.1667, 0.25, 0.0, 0.32, 0.0, 0.2035, 0.1187, 0.1415, 0.0254, 0.0769, 0.0204, 0.0, 0.09, 0.039, 0.0155]
DEBUG4 [28.0, 31.0, 35.0, 52.0, 64.0, 90.0, 120.0, 140.0, 175.0, 175.0, 231.0, 231.0, 278.0, 311.0, 355.0, 364.0, 392.0, 400.0, 400.0, 436.0, 453.0, 460.0]
DEBUG5                  Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                            
data          Western Australia      Australia  24.062338  53.571429   
avg_d_RH                    NaN            NaN        NaN        NaN   
avg_d_precip                NaN            NaN        NaN        NaN   
avg_d_tmp                   NaN            NaN        NaN        NaN   
avg_d_wind                  NaN            NaN        NaN        NaN   

              avg_m_pre

...

new Alaska US
totals [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0.0]
ratios [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
SKIP
new Alaska US
totals [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0.0]
ratios [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
SKIP
ne

Debug 7  2.3325
Debug 0  0.0478 0.1146
DEBUG1 nan Norway 6086.0 304.3
DEBUG2 0.0478 0.0923 0.1146 3/10/2020 29 29
DEBUG3 [0.9512, 0.495, 0.1739, 0.4188, 0.0944, 0.1202, 0.0917, 0.0975, 0.0595, 0.1265, 0.0962, 0.1066, 0.1261, 0.099, 0.0923, 0.0772, 0.0924, 0.1146, 0.0692, 0.067, 0.0376, 0.0441, 0.0478, 0.0584, 0.0433, 0.0335, 0.0247, 0.0313, 0.0377]
DEBUG4 [400.0, 598.0, 702.0, 996.0, 1090.0, 1221.0, 1333.0, 1463.0, 1550.0, 1746.0, 1914.0, 2118.0, 2385.0, 2621.0, 2863.0, 3084.0, 3369.0, 3755.0, 4015.0, 4284.0, 4445.0, 4641.0, 4863.0, 5147.0, 5370.0, 5550.0, 5687.0, 5865.0, 6086.0]
DEBUG5              Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                    NaN         Norway   0.157143  81.246753   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN  

Debug 0  0.07445 0.1245
DEBUG1 nan Sweden 7693.0 384.65
DEBUG2 0.07445 0.099 0.1245 3/11/2020 28 28
DEBUG3 [0.4085, 0.198, 0.3589, 0.1806, 0.0635, 0.0793, 0.0789, 0.0748, 0.1251, 0.139, 0.0757, 0.097, 0.0579, 0.1173, 0.105, 0.1243, 0.0806, 0.1232, 0.0734, 0.0886, 0.101, 0.1154, 0.1255, 0.1011, 0.0509, 0.0601, 0.0551, 0.0676]
DEBUG4 [500.0, 599.0, 814.0, 961.0, 1022.0, 1103.0, 1190.0, 1279.0, 1439.0, 1639.0, 1763.0, 1934.0, 2046.0, 2286.0, 2526.0, 2840.0, 3069.0, 3447.0, 3700.0, 4028.0, 4435.0, 4947.0, 5568.0, 6131.0, 6443.0, 6830.0, 7206.0, 7693.0]
DEBUG5              Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                    NaN         Sweden  -1.398701  77.909091   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN   

Debug 0  0.060700000000000004 0.21395
DEBUG1 Alaska US 65.0 3.25
DEBUG2 0.060700000000000004 0.1522 0.21395 3/20/2020 19 19
DEBUG3 [0.6667, 0.2, 0.1667, 0.0, 0.0, 0.4286, 0.1, -0.0909, 0.9, 0.2105, 0.2174, 0.0714, 0.1667, 0.1429, 0.05, 0.0952, 0.1522, 0.0, 0.2264]
DEBUG4 [5.0, 6.0, 7.0, 7.0, 7.0, 10.0, 10.0, 11.0, 19.0, 23.0, 28.0, 30.0, 35.0, 40.0, 42.0, 46.0, 53.0, 53.0, 65.0]
DEBUG5              Province_State Country_Region  avg_m_tmp   avg_m_RH  \
information                                                        
data                 Alaska             US -16.824675  69.103896   
avg_d_RH                NaN            NaN        NaN        NaN   
avg_d_precip            NaN            NaN        NaN        NaN   
avg_d_tmp               NaN            NaN        NaN        NaN   
avg_d_wind              NaN            NaN        NaN        NaN   

              avg_m_precip  avg_m_wind  Max_Cases  first_7 last relevant date  \
information                                          

Province_State  \
coordinate                  information                                 
(-51.7963, -59.5236)        data          Falkland Islands (Malvinas)   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-41.4545, 145.9707)        data                             Tasmania   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-40.9006, 174.886)         data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-38.4161, -63.6167)        data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-37.8136, 144.9631)        data                             Victoria   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-35.6751, -71.543)         data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
...                                                               ...   
(64.90320724, -164.0353804) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(64.9631, -19.0208)         data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(65.50815459, -151.3907387) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(67.04919196, -159.7503946) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(69.31479216, -153.4836093) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip

In [258]:
look=hopkins_confirmed[[ 'Province_State',  'Country_Region','first_7']]
for row in look.iterrows() :
    if row[0][1]=='data' : 
         print (row[1][0:3])

Province_State     Tasmania
Country_Region    Australia
first_7             1.33333
Name: ((-41.4545, 145.9707), data), dtype: object
Province_State            NaN
Country_Region    New Zealand
first_7                  6.75
Name: ((-40.9006, 174.886), data), dtype: object
Province_State          NaN
Country_Region    Argentina
first_7             2.12903
Name: ((-38.4161, -63.6167), data), dtype: object
Province_State     Victoria
Country_Region    Australia
first_7             2.36111
Name: ((-37.8136, 144.9631), data), dtype: object
Province_State        NaN
Country_Region      Chile
first_7           3.07742
Name: ((-35.6751, -71.543), data), dtype: object
Province_State    Australian Capital Territory
Country_Region                       Australia
first_7                                   8.75
Name: ((-35.4735, 149.0124), data), dtype: object
Province_State    South Australia
Country_Region          Australia
first_7                     1.625
Name: ((-34.9285, 138.6007), data), dty

Name: ((17.0608, -61.7964), data), dtype: object
Province_State                      NaN
Country_Region    Saint Kitts and Nevis
first_7                             NaN
Name: ((17.357822, -62.782998), data), dtype: object
Province_State     NaN
Country_Region    Mali
first_7            NaN
Name: ((17.570692, -3.996166000000001), data), dtype: object
Province_State      NaN
Country_Region    Niger
first_7             NaN
Name: ((17.6078, 8.0817), data), dtype: object
Province_State    Saint Barthelemy
Country_Region              France
first_7                        NaN
Name: ((17.9, -62.8333), data), dtype: object
Province_State    Sint Maarten
Country_Region     Netherlands
first_7                    NaN
Name: ((18.0425, -63.0548), data), dtype: object
Province_State    St Martin
Country_Region       France
first_7                 NaN
Name: ((18.0708, -63.0501), data), dtype: object
Province_State        NaN
Country_Region    Jamaica
first_7               5.5
Name: ((18.1096, -77.2975

Name: ((40.1431, 47.5769), data), dtype: object
Province_State    Beijing
Country_Region      China
first_7           2.16667
Name: ((40.1824, 116.4142), data), dtype: object
Province_State    Xinjiang
Country_Region       China
first_7                3.5
Name: ((41.1129, 85.2401), data), dtype: object
Province_State        NaN
Country_Region    Albania
first_7               4.1
Name: ((41.1533, 20.1683), data), dtype: object
Province_State           NaN
Country_Region    Kyrgyzstan
first_7                   13
Name: ((41.2044, 74.7661), data), dtype: object
Province_State    Liaoning
Country_Region       China
first_7            1.82353
Name: ((41.2956, 122.6085), data), dtype: object
Province_State           NaN
Country_Region    Uzbekistan
first_7              6.16667
Name: ((41.3775, 64.5853), data), dtype: object
Province_State                NaN
Country_Region    North Macedonia
first_7                   2.42857
Name: ((41.6086, 21.7453), data), dtype: object
Province_State      

In [17]:
hopkins_confirmed.to_csv('hopcheck1.csv')

###### Calculate growth factors

In [8]:
hopkins_confirmed 
#hopkins_confirmed.columns



#dataonly=hopkins_confirmed['information']=='data'
#hopconf_data=hopkins_confirmed[dataonly]
#hopconf_data

Province_State  \
coordinate                  information                                 
(-51.7963, -59.5236)        data          Falkland Islands (Malvinas)   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-41.4545, 145.9707)        data                             Tasmania   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-40.9006, 174.886)         data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-38.4161, -63.6167)        data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-37.8136, 144.9631)        data                             Victoria   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(-35.6751, -71.543)         data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
...                                                               ...   
(64.90320724, -164.0353804) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(64.9631, -19.0208)         data                                  NaN   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(65.50815459, -151.3907387) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(67.04919196, -159.7503946) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip                          NaN   
                            avg_d_tmp                             NaN   
                            avg_d_wind                            NaN   
(69.31479216, -153.4836093) data                               Alaska   
                            avg_d_RH                              NaN   
                            avg_d_precip

###### Save file as pickle

In [20]:
pickle_path = RESULT_PATH.format(datetime.now().strftime('%d%m'))
with open(pickle_path, 'wb') as file:
    pickle.dump(hopkins_confirmed, file)